In [1]:
import sys
sys.path.insert(0, '../utils/')

In [2]:
import torch

import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib as mpl
import matplotlib.pyplot as plt

from collections import defaultdict, Counter

%matplotlib inline
mpl.rcParams['figure.dpi']= 500
sns.set_context("notebook")
sns.set(style="white")

In [3]:
from top_genes import latent_dim_participation_in_clusters, indices_of_top_k, select_genes_by_latent_dim, merged_count, mean_of_attention_heads

# Load and preparation

In [4]:
LATENT_DIM = 50

In [5]:
hvg_genes = pd.read_csv('schisto_example/HVG/Schisto_HVG_250.csv')['Unnamed: 0'].values

In [6]:
cellvgae_node_embs = np.load('schisto_example/CellVGAE/cellvgae_node_embs.npy')
cellvgae_umap = np.load('schisto_example/CellVGAE/cellvgae_umap.npy')
cellvgae_clusters = np.load('schisto_example/CellVGAE/cellvgae_clusters.npy')

In [7]:
l1_weight = torch.load('schisto_example/layer_weights/schisto_hidden_layer_1_weight.pt')
l2_weight = torch.load('schisto_example/layer_weights/schisto_hidden_layer_2_weight.pt')
l_mean_weight = torch.load('schisto_example/layer_weights/schisto_hidden_layer_mean_weight.pt')
l_std_weight = torch.load('schisto_example/layer_weights/schisto_hidden_layer_std_weight.pt')

In [8]:
l1_l2 = torch.mm(l1_weight.T, l2_weight.T)

In [9]:
prod_mean = torch.mm(l1_l2, l_mean_weight.T)
prod_std = torch.mm(l1_l2, l_std_weight.T)

In [10]:
merged_mean_layer = mean_of_attention_heads(prod_mean, LATENT_DIM)
merged_std_layer = mean_of_attention_heads(prod_std, LATENT_DIM)

In [11]:
merged_mean_layer.shape

torch.Size([250, 50])

In [12]:
merged_std_layer.shape

torch.Size([250, 50])

# Top genes per cluster

In [13]:
latent_diff_clusters = latent_dim_participation_in_clusters(cellvgae_node_embs, cellvgae_clusters)

In [14]:
latent_diff_clusters_head =  latent_diff_clusters.sort_values(['Cluster','Percentage'],ascending=False).groupby('Cluster').head(10)

In [15]:
cluster_to_genes_mean = defaultdict(list)
cluster_to_genes_std = defaultdict(list)

for index, row in latent_diff_clusters_head.iterrows():
    cl = int(row['Cluster'])
    # Remove abs to look only at the highest negative values
    cluster_to_genes_mean[cl].append(select_genes_by_latent_dim(torch.abs(merged_mean_layer), int(row['Latent dimension']), 15))
    cluster_to_genes_std[cl].append(select_genes_by_latent_dim(torch.abs(merged_std_layer), int(row['Latent dimension']), 15))

In [16]:
cluster_to_genes_mean_merged = {cl : np.concatenate(cluster_to_genes_mean[cl], axis=None) for cl in cluster_to_genes_mean.keys()}
cluster_to_genes_std_merged = {cl : np.concatenate(cluster_to_genes_std[cl], axis=None) for cl in cluster_to_genes_std.keys()}
cluster_to_genes_mean_merged = {cl: Counter(cluster_to_genes_mean_merged[cl].tolist()) for cl in cluster_to_genes_mean_merged.keys()}
cluster_to_genes_std_merged = {cl: Counter(cluster_to_genes_std_merged[cl].tolist()) for cl in cluster_to_genes_std_merged.keys()}

In [17]:
mean_layer_common_genes = [v.most_common(100) for k, v in cluster_to_genes_mean_merged.items()]
std_layer_common_genes = [v.most_common(100) for k, v in cluster_to_genes_std_merged.items()]

In [18]:
mean_layer_count = merged_count(mean_layer_common_genes)
std_layer_count = merged_count(std_layer_common_genes)

In [19]:
mean_layer_count

defaultdict(int,
            {0: 11,
             15: 8,
             139: 6,
             176: 4,
             79: 4,
             83: 6,
             91: 6,
             60: 2,
             141: 4,
             175: 3,
             102: 2,
             68: 4,
             204: 2,
             38: 3,
             40: 3,
             214: 3,
             22: 5,
             167: 3,
             81: 5,
             242: 2,
             109: 2,
             239: 2,
             174: 3,
             191: 6,
             64: 2,
             249: 3,
             21: 2,
             127: 2,
             104: 4,
             164: 2,
             163: 5,
             92: 1,
             146: 4,
             195: 2,
             180: 1,
             62: 1,
             94: 7,
             138: 1,
             74: 2,
             11: 1,
             131: 1,
             218: 1,
             82: 2,
             6: 5,
             13: 4,
             42: 2,
             59: 2,
             117: 2,

In [20]:
genes_per_cluster_mean = [list(zip(hvg_genes[[x[0] for x in lst]], [x[1] for x in lst])) for lst in mean_layer_common_genes]
genes_per_cluster_std = [list(zip(hvg_genes[[x[0] for x in lst]], [x[1] for x in lst])) for lst in std_layer_common_genes]

In [21]:
genes_per_cluster_mean

[[('Smp-161920', 7),
  ('Smp-070380', 4),
  ('Smp-179790', 4),
  ('Smp-083710', 3),
  ('Smp-153730', 3),
  ('Smp-041550', 3),
  ('Smp-206120', 3),
  ('Smp-136370', 2),
  ('Smp-172560', 2),
  ('Smp-152270', 2),
  ('Smp-040460', 2),
  ('Smp-021340', 2),
  ('Smp-080110', 2),
  ('Smp-132080', 2),
  ('Smp-131500', 2),
  ('Smp-043120', 2),
  ('Smp-060160', 2),
  ('Smp-201730', 2),
  ('Smp-043580', 2),
  ('Smp-143000', 2),
  ('Smp-156470', 2),
  ('Smp-049160', 2),
  ('Smp-100570', 2),
  ('Smp-068280', 2),
  ('Smp-159590', 2),
  ('Smp-165240', 2),
  ('Smp-124290', 2),
  ('Smp-067800', 2),
  ('Smp-080840', 2),
  ('Smp-069820', 2),
  ('Smp-143560', 2),
  ('Smp-015440', 1),
  ('Smp-033620', 1),
  ('Smp-158680', 1),
  ('Smp-141700', 1),
  ('Smp-146900', 1),
  ('Smp-010250', 1),
  ('Smp-019950', 1),
  ('Smp-200240', 1),
  ('Smp-051920', 1),
  ('Smp-063500', 1),
  ('Smp-144550', 1),
  ('Smp-080740', 1),
  ('Smp-203410', 1),
  ('Smp-187430', 1),
  ('Smp-074940', 1),
  ('Smp-054730', 1),
  ('Smp-19723

# Highest weights

In [22]:
vals, inds = torch.topk(torch.flatten(merged_mean_layer), k=150)

In [23]:
inds_2d = []
for ind in inds:
    if ind < LATENT_DIM:
        inds_2d.append((0, ind.item()))
    else:
        x = ind // LATENT_DIM
        inds_2d.append((x.item(), (ind - x * LATENT_DIM).item()))

In [24]:
inds_2d_first_component = [x[0] for x in inds_2d]
max_genes = hvg_genes[inds_2d_first_component].tolist()

In [25]:
len(set(max_genes))

104

In [26]:
max_genes

['Smp-161920',
 'Smp-161920',
 'Smp-161920',
 'Smp-041350',
 'Smp-158680',
 'Smp-059680',
 'Smp-146900',
 'Smp-161920',
 'Smp-204160',
 'Smp-150380',
 'Smp-025750',
 'Smp-145370',
 'Smp-200520',
 'Smp-010250',
 'Smp-041550',
 'Smp-072460',
 'Smp-091660',
 'Smp-025750',
 'Smp-030020',
 'Smp-044680',
 'Smp-032000',
 'Smp-079810',
 'Smp-090830',
 'Smp-104370',
 'Smp-204130',
 'Smp-020480',
 'Smp-162770',
 'Smp-124290',
 'Smp-068240',
 'Smp-121890',
 'Smp-126750',
 'Smp-083710',
 'Smp-019950',
 'Smp-070380',
 'Smp-161920',
 'Smp-065650',
 'Smp-038950',
 'Smp-074940',
 'Smp-199840',
 'Smp-059570',
 'Smp-049240',
 'Smp-002930',
 'Smp-132080',
 'Smp-149620',
 'Smp-065650',
 'Smp-204730',
 'Smp-033620',
 'Smp-158740',
 'Smp-134000',
 'Smp-021340',
 'Smp-015670',
 'Smp-123030',
 'Smp-067800',
 'Smp-104860',
 'Smp-036950',
 'Smp-061050',
 'Smp-009070',
 'Smp-153730',
 'Smp-161920',
 'Smp-172560',
 'Smp-187430',
 'Smp-025750',
 'Smp-038960',
 'Smp-010250',
 'Smp-152270',
 'Smp-060490',
 'Smp-0674